In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import os

import threading
import queue
import shutil

from glob import glob
from re import sub, findall

## Reading the txt file that categorize the data

In [4]:
txt_files = glob('./datasets/faces/*.txt')
txt_files

['./datasets/faces/fold_2_data.txt',
 './datasets/faces/fold_4_data.txt',
 './datasets/faces/fold_0_data.txt',
 './datasets/faces/fold_3_data.txt',
 './datasets/faces/fold_1_data.txt']

In [6]:
list_dataframes = []
for file in txt_files:
    df = pd.read_csv(file, sep='\t')
    list_dataframes.append(df)
first_dataset_df = pd.concat(list_dataframes, axis=0, ignore_index=True)
first_dataset_df

user_id                original_image  face_id        age gender  \
0       64504106@N06  11831304783_488d6c3a6d_o.jpg      911     (0, 2)      m   
1       64504106@N06  11849646776_35253e988f_o.jpg      911     (0, 2)      m   
2       64504106@N06  11848166326_57b03f535e_o.jpg      911     (0, 2)      m   
3       64504106@N06  11812546385_bb4d020dde_o.jpg      911     (0, 2)      m   
4       64504106@N06  11831118625_81dcc72e75_o.jpg      912   (38, 43)      m   
...              ...                           ...      ...        ...    ...   
19365   35953373@N04   9496952502_4e87cc8b60_o.jpg      907   (15, 20)      m   
19366  104937236@N08  11852401355_e54eba57b6_o.jpg      908   (27, 32)      f   
19367   37404707@N08  11128849885_6a56d25762_o.jpg      909    (8, 12)    NaN   
19368   37404707@N08  11182710183_e75c82dde1_o.jpg      910  (60, 100)    NaN   
19369   37404707@N08  11129028253_2e9d0c4b18_o.jpg      909    (8, 12)    NaN   

          x     y    dx    dy  tilt_ang  fiducial_yaw_angle  fiducial_score  
0       438   914   605   606       -90                   0             123  
1        19   712  1944  1736      -105                   0              86  
2       382   680  1785  1768       -80                   0              14  
3       608   948   893   892      -105                   0               8  
4        23   150   508   508       -90                   0              79  
...     ...   ...   ...   ...       ...                 ...             ...  
19365  1318   184   643   644         5                 -30              78  
19366  1310   725   573   573       -90                   0              90  
19367   820  1099   364   364        -5                   0             103  
19368  1080   661   376   376        -5                   0              61  
19369   318   349   281   280        10                   0               6  

[19370 rows x 12 columns]

### Check if some images do not have age data

In [9]:
first_dataset_df['age'].isnull().sum()

0

In [15]:
first_dataset_df = first_dataset_df[first_dataset_df['age'] != 'None']

### Get all the ages and create folders for them

In [16]:
first_dataset_df['age'].unique()

array(['(0, 2)', '(38, 43)', '(25, 32)', '(60, 100)', '(4, 6)',
       '(48, 53)', '(8, 12)', '23', '3', '(15, 20)', '57', '56', '2',
       '35', '55', '22', '13', '45', '29', '(38, 48)', '32', '58', '36',
       '34', '42', '(38, 42)', '46', '(27, 32)', '(8, 23)'], dtype=object)

In [3]:
ages = [
    '0_2',
    '3_6',
    '7_13',
    '14_20',
    '21_32',
    '33_43',
    '44_53',
    '54_100'
]

In [57]:
def create_folder_column(age):
    if '(' in age:
        age = findall(r'\((\d+), ?(\d+)\)', age)
        age = list(map(int, age[0]))
    else:
        age = [int(age), int(age)]
    
    for a in ages:
        age_slice = a.split('_')
        age_slice = list(map(int, age_slice))
        if age_slice[0] <= age[0] and age[1] <= age_slice[1]:
            return a
    return None

In [58]:
first_dataset_df['folder'] = first_dataset_df['age'].apply(create_folder_column)
first_dataset_df

<ipython-input-58-607c1ae3ca61>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  first_dataset_df['folder'] = first_dataset_df['age'].apply(create_folder_column)


user_id                original_image  face_id        age gender  \
0       64504106@N06  11831304783_488d6c3a6d_o.jpg      911     (0, 2)      m   
1       64504106@N06  11849646776_35253e988f_o.jpg      911     (0, 2)      m   
2       64504106@N06  11848166326_57b03f535e_o.jpg      911     (0, 2)      m   
3       64504106@N06  11812546385_bb4d020dde_o.jpg      911     (0, 2)      m   
4       64504106@N06  11831118625_81dcc72e75_o.jpg      912   (38, 43)      m   
...              ...                           ...      ...        ...    ...   
19365   35953373@N04   9496952502_4e87cc8b60_o.jpg      907   (15, 20)      m   
19366  104937236@N08  11852401355_e54eba57b6_o.jpg      908   (27, 32)      f   
19367   37404707@N08  11128849885_6a56d25762_o.jpg      909    (8, 12)    NaN   
19368   37404707@N08  11182710183_e75c82dde1_o.jpg      910  (60, 100)    NaN   
19369   37404707@N08  11129028253_2e9d0c4b18_o.jpg      909    (8, 12)    NaN   

          x     y    dx    dy  tilt_ang  fiducial_yaw_angle  fiducial_score  \
0       438   914   605   606       -90                   0             123   
1        19   712  1944  1736      -105                   0              86   
2       382   680  1785  1768       -80                   0              14   
3       608   948   893   892      -105                   0               8   
4        23   150   508   508       -90                   0              79   
...     ...   ...   ...   ...       ...                 ...             ...   
19365  1318   184   643   644         5                 -30              78   
19366  1310   725   573   573       -90                   0              90   
19367   820  1099   364   364        -5                   0             103   
19368  1080   661   376   376        -5                   0              61   
19369   318   349   281   280        10                   0               6   

       folder  
0         0_2  
1         0_2  
2         0_2  
3         0_2  
4       33_43  
...       ...  
19365   14_20  
19366   21_32  
19367    7_13  
19368  54_100  
19369    7_13  

[18622 rows x 13 columns]

In [62]:
for age in ages:
    os.mkdir('./datasets/data/train/'+age)
    os.mkdir('./datasets/data/test/'+age)
    os.mkdir('./datasets/data/val/'+age)

### Spliting the dataset for train, test and val

In [64]:
train, validate, test = np.split(first_dataset_df.sample(frac=1, random_state=42), [int(.8*len(first_dataset_df)), int(.9*len(first_dataset_df))])

In [69]:
print(len(train))
print(len(validate))
print(len(test))

14897
1862
1863


### Writing the images into the right folders

In [8]:
class FileCopy(threading.Thread):
    def __init__(self, queue, files, dataset):
        threading.Thread.__init__(self)
        self.queue = queue
        self._files = files
        self._dest = './datasets/data/' + dataset

    def run(self):
        try:
            for file in self._files:  
                try:
                    shutil.copyfile(file[0], self._dest + '/' + file[1])
                except IOError as e:
                    self.queue.put(e)
                else:
                    self.queue.put(file)
        finally:
            self.queue.put(None)

In [77]:
def generate_source_dest(user_id, face_id, original_image, folder_age):
    return (
        f'./datasets/faces/{user_id}/coarse_tilt_aligned_face.{face_id}.{original_image}',
        f'{folder_age}/{face_id}.{original_image}'
    )
train['source_dest'] = train.apply(lambda x: generate_source_dest(x['user_id'], x['face_id'], x['original_image'], x['folder']), axis=1)

In [81]:
train['source_dest'][0]

('./datasets/faces/64504106@N06/coarse_tilt_aligned_face.911.11831304783_488d6c3a6d_o.jpg',
 '0_2/911.11831304783_488d6c3a6d_o.jpg')

In [95]:
def run_thread(dataset):
    if dataset == 'train':
        df = train
    elif dataset == 'test':
        df = test
    else:
        df = validate
    
    df['source_dest'] = df.apply(lambda x: generate_source_dest(x['user_id'], x['face_id'], x['original_image'], x['folder']), axis=1)
    files = list(df['source_dest'])
    _queue = queue.Queue()
    thread = FileCopy(_queue, files, dataset)
    thread.start()
    while True:
        x = _queue.get()
        if x is None:
            break
        print(x)
    thread.join()

In [96]:
run_thread('train')
run_thread('test')
run_thread('val')

('./datasets/faces/30601258@N03/coarse_tilt_aligned_face.2.9902297806_c4a3efea96_o.jpg', '21_32/2.9902297806_c4a3efea96_o.jpg')
('./datasets/faces/10897942@N03/coarse_tilt_aligned_face.634.10372351604_cc840d44dc_o.jpg', '21_32/634.10372351604_cc840d44dc_o.jpg')
('./datasets/faces/9017386@N06/coarse_tilt_aligned_face.207.8504680971_71a30dc5b2_o.jpg', '3_6/207.8504680971_71a30dc5b2_o.jpg')
('./datasets/faces/115153697@N06/coarse_tilt_aligned_face.628.12096915803_550fa74573_o.jpg', '21_32/628.12096915803_550fa74573_o.jpg')
('./datasets/faces/113445054@N07/coarse_tilt_aligned_face.1347.11763624023_8f875abee4_o.jpg', '54_100/1347.11763624023_8f875abee4_o.jpg')
('./datasets/faces/10406201@N05/coarse_tilt_aligned_face.282.11457837594_91a8bc1024_o.jpg', '21_32/282.11457837594_91a8bc1024_o.jpg')
('./datasets/faces/10440927@N07/coarse_tilt_aligned_face.784.12092116754_82ed6c368f_o.jpg', '33_43/784.12092116754_82ed6c368f_o.jpg')
('./datasets/faces/115321157@N03/coarse_tilt_aligned_face.1748.12123

('./datasets/faces/29671106@N00/coarse_tilt_aligned_face.194.11193006113_56900fc380_o.jpg', '3_6/194.11193006113_56900fc380_o.jpg')
('./datasets/faces/20632896@N03/coarse_tilt_aligned_face.557.9826187946_6785be2759_o.jpg', '7_13/557.9826187946_6785be2759_o.jpg')
('./datasets/faces/113715068@N06/coarse_tilt_aligned_face.1410.11865987785_8104dd362e_o.jpg', '14_20/1410.11865987785_8104dd362e_o.jpg')
('./datasets/faces/37303189@N08/coarse_tilt_aligned_face.84.8277549377_903b5be21d_o.jpg', '0_2/84.8277549377_903b5be21d_o.jpg')
('./datasets/faces/60251856@N05/coarse_tilt_aligned_face.1512.11916778744_78db9436a2_o.jpg', '21_32/1512.11916778744_78db9436a2_o.jpg')
('./datasets/faces/10543088@N02/coarse_tilt_aligned_face.678.10044782294_1cf6f8871e_o.jpg', '44_53/678.10044782294_1cf6f8871e_o.jpg')
('./datasets/faces/62501130@N02/coarse_tilt_aligned_face.100.11305772974_b8ca7101b5_o.jpg', '21_32/100.11305772974_b8ca7101b5_o.jpg')
('./datasets/faces/37303189@N08/coarse_tilt_aligned_face.84.87789802

('./datasets/faces/29671106@N00/coarse_tilt_aligned_face.186.9202432000_de54318980_o.jpg', '0_2/186.9202432000_de54318980_o.jpg')
('./datasets/faces/10280355@N07/coarse_tilt_aligned_face.1880.11368076403_0e6cda02bd_o.jpg', '44_53/1880.11368076403_0e6cda02bd_o.jpg')
('./datasets/faces/37303189@N08/coarse_tilt_aligned_face.84.8863540886_5d4be8151c_o.jpg', '0_2/84.8863540886_5d4be8151c_o.jpg')
('./datasets/faces/28754132@N06/coarse_tilt_aligned_face.610.11612824814_f4beed5182_o.jpg', '7_13/610.11612824814_f4beed5182_o.jpg')
('./datasets/faces/34158582@N02/coarse_tilt_aligned_face.401.10282893003_4a27deaed0_o.jpg', '0_2/401.10282893003_4a27deaed0_o.jpg')
('./datasets/faces/115321157@N03/coarse_tilt_aligned_face.1744.12112820644_5007136eae_o.jpg', '3_6/1744.12112820644_5007136eae_o.jpg')
('./datasets/faces/29671106@N00/coarse_tilt_aligned_face.186.11560287505_f2b6e4604a_o.jpg', '0_2/186.11560287505_f2b6e4604a_o.jpg')
('./datasets/faces/114841417@N06/coarse_tilt_aligned_face.482.12068690463_

('./datasets/faces/7648211@N03/coarse_tilt_aligned_face.456.10198681976_25ec8d2d38_o.jpg', '0_2/456.10198681976_25ec8d2d38_o.jpg')
('./datasets/faces/64504106@N06/coarse_tilt_aligned_face.912.11840729303_d1496ef73e_o.jpg', '33_43/912.11840729303_d1496ef73e_o.jpg')
('./datasets/faces/29671106@N00/coarse_tilt_aligned_face.186.9398101586_7a95a1245c_o.jpg', '0_2/186.9398101586_7a95a1245c_o.jpg')
('./datasets/faces/31183835@N08/coarse_tilt_aligned_face.2099.11653072003_0b66a7303b_o.jpg', '33_43/2099.11653072003_0b66a7303b_o.jpg')
('./datasets/faces/20254529@N04/coarse_tilt_aligned_face.18.11509490676_d78ee05fab_o.jpg', '21_32/18.11509490676_d78ee05fab_o.jpg')
('./datasets/faces/30601258@N03/coarse_tilt_aligned_face.2.10424721415_2a5ab30b00_o.jpg', '21_32/2.10424721415_2a5ab30b00_o.jpg')
('./datasets/faces/31040257@N06/coarse_tilt_aligned_face.359.9726807287_a2981c0a9d_o.jpg', '21_32/359.9726807287_a2981c0a9d_o.jpg')
('./datasets/faces/48647239@N03/coarse_tilt_aligned_face.1519.11838932476_8

('./datasets/faces/7636528@N03/coarse_tilt_aligned_face.1051.11486520395_65cb63af61_o.jpg', '0_2/1051.11486520395_65cb63af61_o.jpg')
('./datasets/faces/37303189@N08/coarse_tilt_aligned_face.84.8863049438_bec978af41_o.jpg', '0_2/84.8863049438_bec978af41_o.jpg')
('./datasets/faces/28468602@N06/coarse_tilt_aligned_face.2218.11538547525_0ef66c0283_o.jpg', '0_2/2218.11538547525_0ef66c0283_o.jpg')
('./datasets/faces/7464014@N04/coarse_tilt_aligned_face.968.10339749714_f2db0688f5_o.jpg', '21_32/968.10339749714_f2db0688f5_o.jpg')
('./datasets/faces/7398884@N04/coarse_tilt_aligned_face.1649.8725918313_979c27e4a4_o.jpg', '14_20/1649.8725918313_979c27e4a4_o.jpg')
('./datasets/faces/7636528@N03/coarse_tilt_aligned_face.1050.11486879925_4f1e6e9a8a_o.jpg', '7_13/1050.11486879925_4f1e6e9a8a_o.jpg')
('./datasets/faces/50739822@N00/coarse_tilt_aligned_face.1365.11049496716_ed9b9d425b_o.jpg', '7_13/1365.11049496716_ed9b9d425b_o.jpg')
('./datasets/faces/8007224@N07/coarse_tilt_aligned_face.2115.118670679

...

('./datasets/faces/33627988@N04/coarse_tilt_aligned_face.1946.11642281693_02b0f20c38_o.jpg', '33_43/1946.11642281693_02b0f20c38_o.jpg')
('./datasets/faces/8187011@N06/coarse_tilt_aligned_face.989.9489161267_0682770ffa_o.jpg', '3_6/989.9489161267_0682770ffa_o.jpg')
('./datasets/faces/82152000@N00/coarse_tilt_aligned_face.726.11899063746_eeb594b242_o.jpg', '7_13/726.11899063746_eeb594b242_o.jpg')
('./datasets/faces/115321157@N03/coarse_tilt_aligned_face.1747.12111049976_61d6b1d59d_o.jpg', '21_32/1747.12111049976_61d6b1d59d_o.jpg')
('./datasets/faces/10743505@N04/coarse_tilt_aligned_face.1557.10933398056_fbb4e32d5a_o.jpg', '44_53/1557.10933398056_fbb4e32d5a_o.jpg')
('./datasets/faces/10897942@N03/coarse_tilt_aligned_face.632.10372349255_06b11b35e8_o.jpg', '21_32/632.10372349255_06b11b35e8_o.jpg')
('./datasets/faces/113528649@N08/coarse_tilt_aligned_face.333.11764353383_7876699f95_o.jpg', '7_13/333.11764353383_7876699f95_o.jpg')
('./datasets/faces/10406201@N05/coarse_tilt_aligned_face.265.

('./datasets/faces/10354155@N05/coarse_tilt_aligned_face.421.11937896894_147ae7c049_o.jpg', '33_43/421.11937896894_147ae7c049_o.jpg')
('./datasets/faces/9017386@N06/coarse_tilt_aligned_face.207.8643077180_fa6bafcd8a_o.jpg', '3_6/207.8643077180_fa6bafcd8a_o.jpg')
('./datasets/faces/114841417@N06/coarse_tilt_aligned_face.486.12060324573_13469841c9_o.jpg', '14_20/486.12060324573_13469841c9_o.jpg')
('./datasets/faces/20632896@N03/coarse_tilt_aligned_face.573.9830220974_d33df1c978_o.jpg', '7_13/573.9830220974_d33df1c978_o.jpg')
('./datasets/faces/7636528@N03/coarse_tilt_aligned_face.1051.11486630646_8acb9db15d_o.jpg', '0_2/1051.11486630646_8acb9db15d_o.jpg')
('./datasets/faces/50739822@N00/coarse_tilt_aligned_face.1364.8257091256_1163eeab66_o.jpg', '7_13/1364.8257091256_1163eeab66_o.jpg')
('./datasets/faces/115321157@N03/coarse_tilt_aligned_face.1751.12110803894_f8e8d05f5f_o.jpg', '54_100/1751.12110803894_f8e8d05f5f_o.jpg')
('./datasets/faces/10148140@N07/coarse_tilt_aligned_face.1964.91699

('./datasets/faces/37303189@N08/coarse_tilt_aligned_face.84.11436877514_9b7e41c2b0_o.jpg', '0_2/84.11436877514_9b7e41c2b0_o.jpg')
('./datasets/faces/11008464@N06/coarse_tilt_aligned_face.970.11307705893_5921f3425d_o.jpg', '0_2/970.11307705893_5921f3425d_o.jpg')
('./datasets/faces/30601258@N03/coarse_tilt_aligned_face.2.10204632316_ed078f959f_o.jpg', '21_32/2.10204632316_ed078f959f_o.jpg')
('./datasets/faces/113445054@N07/coarse_tilt_aligned_face.1327.11764019623_8ffb8ff4f5_o.jpg', '21_32/1327.11764019623_8ffb8ff4f5_o.jpg')
('./datasets/faces/7464014@N04/coarse_tilt_aligned_face.962.10143750874_7bdf0fc0ea_o.jpg', '21_32/962.10143750874_7bdf0fc0ea_o.jpg')
('./datasets/faces/8410632@N03/coarse_tilt_aligned_face.1784.11848578636_e4604e7486_o.jpg', '0_2/1784.11848578636_e4604e7486_o.jpg')
('./datasets/faces/64504106@N06/coarse_tilt_aligned_face.914.11841100224_84091f241e_o.jpg', '54_100/914.11841100224_84091f241e_o.jpg')
('./datasets/faces/10148140@N07/coarse_tilt_aligned_face.1956.10318677

('./datasets/faces/7411850@N04/coarse_tilt_aligned_face.466.11106586114_e5f78537a9_o.jpg', '21_32/466.11106586114_e5f78537a9_o.jpg')
('./datasets/faces/115021413@N07/coarse_tilt_aligned_face.949.12059582783_caa3f76d46_o.jpg', '7_13/949.12059582783_caa3f76d46_o.jpg')
('./datasets/faces/113445054@N07/coarse_tilt_aligned_face.1325.11763402993_1dee110030_o.jpg', '21_32/1325.11763402993_1dee110030_o.jpg')
('./datasets/faces/28754132@N06/coarse_tilt_aligned_face.608.9365895689_13f884ff30_o.jpg', '7_13/608.9365895689_13f884ff30_o.jpg')
('./datasets/faces/11008464@N06/coarse_tilt_aligned_face.970.11548364405_5311516c71_o.jpg', '0_2/970.11548364405_5311516c71_o.jpg')
('./datasets/faces/10148140@N07/coarse_tilt_aligned_face.1956.10318634816_9b9ea85b52_o.jpg', '33_43/1956.10318634816_9b9ea85b52_o.jpg')
('./datasets/faces/16886060@N03/coarse_tilt_aligned_face.1913.11394449655_76f4bb4202_o.jpg', '21_32/1913.11394449655_76f4bb4202_o.jpg')
('./datasets/faces/9855553@N08/coarse_tilt_aligned_face.1574.

('./datasets/faces/9965452@N08/coarse_tilt_aligned_face.984.9256441153_3e0c5c1e25_o.jpg', '33_43/984.9256441153_3e0c5c1e25_o.jpg')
('./datasets/faces/29671106@N00/coarse_tilt_aligned_face.194.11192916406_3288dd6c8f_o.jpg', '3_6/194.11192916406_3288dd6c8f_o.jpg')
('./datasets/faces/7890646@N03/coarse_tilt_aligned_face.1392.10693545494_08c88aa037_o.jpg', '33_43/1392.10693545494_08c88aa037_o.jpg')
('./datasets/faces/10792106@N03/coarse_tilt_aligned_face.528.11058119825_c5472f5eae_o.jpg', '33_43/528.11058119825_c5472f5eae_o.jpg')
('./datasets/faces/7464014@N04/coarse_tilt_aligned_face.966.10091725896_80ab2c3981_o.jpg', '44_53/966.10091725896_80ab2c3981_o.jpg')
('./datasets/faces/16886060@N03/coarse_tilt_aligned_face.1906.11376610043_010f155dc9_o.jpg', '33_43/1906.11376610043_010f155dc9_o.jpg')
('./datasets/faces/113804525@N05/coarse_tilt_aligned_face.324.11846400264_2467848699_o.jpg', '54_100/324.11846400264_2467848699_o.jpg')
('./datasets/faces/9017386@N06/coarse_tilt_aligned_face.220.107

## Moving the UTKFace dataset

In [127]:
faces = glob('./datasets/archive/UTKFace/*.jpg')
faces_ages = []
for face in faces:
    age = face.split('_')[0]
    age = age.split('/')[-1]
    filename = face.split('/')[-1]
    
    age_slice = None
    age = int(age)
    for a in ages:
        _age = a.split('_')
        if int(_age[0]) <= age <= int(_age[1]):
            age_slice = a
    
    dest = f'{age_slice}/{filename}'

    faces_ages.append((face, dest))
faces_ages = np.array(faces_ages)
len(faces_ages)

23708

In [128]:
utk_train, utk_val, utk_test = np.split(faces_ages, [int(.8*len(faces_ages)), int(.9*len(faces_ages))])

In [129]:
print(len(utk_train))
print(len(utk_val))
print(len(utk_test))

18966
2371
2371


In [132]:
utk_train

array([['./datasets/archive/UTKFace/29_0_4_20170103235130284.jpg.chip.jpg',
        '21_32/29_0_4_20170103235130284.jpg.chip.jpg'],
       ['./datasets/archive/UTKFace/60_1_4_20170103230632265.jpg.chip.jpg',
        '54_100/60_1_4_20170103230632265.jpg.chip.jpg'],
       ['./datasets/archive/UTKFace/75_1_0_20170110182543266.jpg.chip.jpg',
        '54_100/75_1_0_20170110182543266.jpg.chip.jpg'],
       ...,
       ['./datasets/archive/UTKFace/20_0_0_20170117140133828.jpg.chip.jpg',
        '14_20/20_0_0_20170117140133828.jpg.chip.jpg'],
       ['./datasets/archive/UTKFace/36_1_1_20170116175558494.jpg.chip.jpg',
        '33_43/36_1_1_20170116175558494.jpg.chip.jpg'],
       ['./datasets/archive/UTKFace/32_0_1_20170117172950046.jpg.chip.jpg',
        '21_32/32_0_1_20170117172950046.jpg.chip.jpg']], dtype='<U65')

In [131]:
def run_utk_thread(dataset, dest):
    files = dataset
    _queue = queue.Queue()
    thread = FileCopy(_queue, files, dest)
    thread.start()
    while True:
        x = _queue.get()
        if x is None:
            break
        print(x)
    thread.join()

In [133]:
run_utk_thread(utk_train, 'train')
run_utk_thread(utk_val, 'val')
run_utk_thread(utk_test, 'test')

['./datasets/archive/UTKFace/29_0_4_20170103235130284.jpg.chip.jpg'
 '21_32/29_0_4_20170103235130284.jpg.chip.jpg']
['./datasets/archive/UTKFace/60_1_4_20170103230632265.jpg.chip.jpg'
 '54_100/60_1_4_20170103230632265.jpg.chip.jpg']
['./datasets/archive/UTKFace/75_1_0_20170110182543266.jpg.chip.jpg'
 '54_100/75_1_0_20170110182543266.jpg.chip.jpg']
['./datasets/archive/UTKFace/15_1_2_20170102234824195.jpg.chip.jpg'
 '14_20/15_1_2_20170102234824195.jpg.chip.jpg']
['./datasets/archive/UTKFace/22_1_0_20170105002545990.jpg.chip.jpg'
 '21_32/22_1_0_20170105002545990.jpg.chip.jpg']
['./datasets/archive/UTKFace/35_1_1_20170112230726789.jpg.chip.jpg'
 '33_43/35_1_1_20170112230726789.jpg.chip.jpg']
['./datasets/archive/UTKFace/26_0_0_20170104201228553.jpg.chip.jpg'
 '21_32/26_0_0_20170104201228553.jpg.chip.jpg']
['./datasets/archive/UTKFace/25_0_1_20170117195252189.jpg.chip.jpg'
 '21_32/25_0_1_20170117195252189.jpg.chip.jpg']
['./datasets/archive/UTKFace/27_0_2_20170119193329569.jpg.chip.jpg'
 '

['./datasets/archive/UTKFace/44_1_0_20170104210419052.jpg.chip.jpg'
 '44_53/44_1_0_20170104210419052.jpg.chip.jpg']
['./datasets/archive/UTKFace/18_0_0_20170117175643037.jpg.chip.jpg'
 '14_20/18_0_0_20170117175643037.jpg.chip.jpg']
['./datasets/archive/UTKFace/31_0_1_20170117165741027.jpg.chip.jpg'
 '21_32/31_0_1_20170117165741027.jpg.chip.jpg']
['./datasets/archive/UTKFace/23_0_1_20170113133721489.jpg.chip.jpg'
 '21_32/23_0_1_20170113133721489.jpg.chip.jpg']
['./datasets/archive/UTKFace/38_0_0_20170109012846030.jpg.chip.jpg'
 '33_43/38_0_0_20170109012846030.jpg.chip.jpg']
['./datasets/archive/UTKFace/23_1_3_20170104222248295.jpg.chip.jpg'
 '21_32/23_1_3_20170104222248295.jpg.chip.jpg']
['./datasets/archive/UTKFace/40_0_1_20170116233052810.jpg.chip.jpg'
 '33_43/40_0_1_20170116233052810.jpg.chip.jpg']
['./datasets/archive/UTKFace/21_1_2_20161219221949111.jpg.chip.jpg'
 '21_32/21_1_2_20161219221949111.jpg.chip.jpg']
['./datasets/archive/UTKFace/55_0_0_20170117155039029.jpg.chip.jpg'
 '54

['./datasets/archive/UTKFace/1_0_4_20161221195115664.jpg.chip.jpg'
 '0_2/1_0_4_20161221195115664.jpg.chip.jpg']
['./datasets/archive/UTKFace/63_0_0_20170104213557957.jpg.chip.jpg'
 '54_100/63_0_0_20170104213557957.jpg.chip.jpg']
['./datasets/archive/UTKFace/31_0_1_20170117203020591.jpg.chip.jpg'
 '21_32/31_0_1_20170117203020591.jpg.chip.jpg']
['./datasets/archive/UTKFace/42_1_2_20170116161958086.jpg.chip.jpg'
 '33_43/42_1_2_20170116161958086.jpg.chip.jpg']
['./datasets/archive/UTKFace/26_1_1_20170116231937264.jpg.chip.jpg'
 '21_32/26_1_1_20170116231937264.jpg.chip.jpg']
['./datasets/archive/UTKFace/51_0_3_20170119205627558.jpg.chip.jpg'
 '44_53/51_0_3_20170119205627558.jpg.chip.jpg']
['./datasets/archive/UTKFace/26_0_1_20170113154809050.jpg.chip.jpg'
 '21_32/26_0_1_20170113154809050.jpg.chip.jpg']
['./datasets/archive/UTKFace/50_1_3_20170117153134813.jpg.chip.jpg'
 '44_53/50_1_3_20170117153134813.jpg.chip.jpg']
['./datasets/archive/UTKFace/28_0_1_20170117021406043.jpg.chip.jpg'
 '21_32

['./datasets/archive/UTKFace/26_0_3_20170119184306231.jpg.chip.jpg'
 '21_32/26_0_3_20170119184306231.jpg.chip.jpg']
['./datasets/archive/UTKFace/28_1_2_20170116161343328.jpg.chip.jpg'
 '21_32/28_1_2_20170116161343328.jpg.chip.jpg']
['./datasets/archive/UTKFace/48_0_0_20170109012405234.jpg.chip.jpg'
 '44_53/48_0_0_20170109012405234.jpg.chip.jpg']
['./datasets/archive/UTKFace/26_0_3_20170119181428332.jpg.chip.jpg'
 '21_32/26_0_3_20170119181428332.jpg.chip.jpg']
['./datasets/archive/UTKFace/8_0_0_20170110215559811.jpg.chip.jpg'
 '7_13/8_0_0_20170110215559811.jpg.chip.jpg']
['./datasets/archive/UTKFace/27_0_1_20170113133402529.jpg.chip.jpg'
 '21_32/27_0_1_20170113133402529.jpg.chip.jpg']
['./datasets/archive/UTKFace/10_1_0_20170109204338404.jpg.chip.jpg'
 '7_13/10_1_0_20170109204338404.jpg.chip.jpg']
['./datasets/archive/UTKFace/26_0_0_20170113182320758.jpg.chip.jpg'
 '21_32/26_0_0_20170113182320758.jpg.chip.jpg']
['./datasets/archive/UTKFace/31_1_1_20170116023825964.jpg.chip.jpg'
 '21_32/

['./datasets/archive/UTKFace/59_0_0_20170111195403793.jpg.chip.jpg'
 '54_100/59_0_0_20170111195403793.jpg.chip.jpg']
['./datasets/archive/UTKFace/26_0_0_20170117201116334.jpg.chip.jpg'
 '21_32/26_0_0_20170117201116334.jpg.chip.jpg']
['./datasets/archive/UTKFace/1_1_2_20161219192458643.jpg.chip.jpg'
 '0_2/1_1_2_20161219192458643.jpg.chip.jpg']
['./datasets/archive/UTKFace/1_0_0_20170110211537870.jpg.chip.jpg'
 '0_2/1_0_0_20170110211537870.jpg.chip.jpg']
['./datasets/archive/UTKFace/74_0_2_20170105174346668.jpg.chip.jpg'
 '54_100/74_0_2_20170105174346668.jpg.chip.jpg']
['./datasets/archive/UTKFace/43_0_0_20170104204257115.jpg.chip.jpg'
 '33_43/43_0_0_20170104204257115.jpg.chip.jpg']
['./datasets/archive/UTKFace/65_0_0_20170103183632050.jpg.chip.jpg'
 '54_100/65_0_0_20170103183632050.jpg.chip.jpg']
['./datasets/archive/UTKFace/40_1_1_20170109003603180.jpg.chip.jpg'
 '33_43/40_1_1_20170109003603180.jpg.chip.jpg']
['./datasets/archive/UTKFace/28_1_4_20170117202604343.jpg.chip.jpg'
 '21_32/2

...

['./datasets/archive/UTKFace/65_1_0_20170110175333844.jpg.chip.jpg'
 '54_100/65_1_0_20170110175333844.jpg.chip.jpg']
['./datasets/archive/UTKFace/26_0_0_20170117003319885.jpg.chip.jpg'
 '21_32/26_0_0_20170117003319885.jpg.chip.jpg']
['./datasets/archive/UTKFace/8_1_0_20170116200940428.jpg.chip.jpg'
 '7_13/8_1_0_20170116200940428.jpg.chip.jpg']
['./datasets/archive/UTKFace/28_0_3_20170119194927932.jpg.chip.jpg'
 '21_32/28_0_3_20170119194927932.jpg.chip.jpg']
['./datasets/archive/UTKFace/23_1_4_20170103223102032.jpg.chip.jpg'
 '21_32/23_1_4_20170103223102032.jpg.chip.jpg']
['./datasets/archive/UTKFace/23_1_3_20170104222242439.jpg.chip.jpg'
 '21_32/23_1_3_20170104222242439.jpg.chip.jpg']
['./datasets/archive/UTKFace/33_1_1_20170116024837534.jpg.chip.jpg'
 '33_43/33_1_1_20170116024837534.jpg.chip.jpg']
['./datasets/archive/UTKFace/1_0_0_20170109194042219.jpg.chip.jpg'
 '0_2/1_0_0_20170109194042219.jpg.chip.jpg']
['./datasets/archive/UTKFace/58_0_0_20170111195852891.jpg.chip.jpg'
 '54_100/5

['./datasets/archive/UTKFace/43_1_3_20170119204557143.jpg.chip.jpg'
 '33_43/43_1_3_20170119204557143.jpg.chip.jpg']
['./datasets/archive/UTKFace/26_1_1_20170116175448301.jpg.chip.jpg'
 '21_32/26_1_1_20170116175448301.jpg.chip.jpg']
['./datasets/archive/UTKFace/42_0_0_20170117130005462.jpg.chip.jpg'
 '33_43/42_0_0_20170117130005462.jpg.chip.jpg']
['./datasets/archive/UTKFace/4_1_4_20161223231735684.jpg.chip.jpg'
 '3_6/4_1_4_20161223231735684.jpg.chip.jpg']
['./datasets/archive/UTKFace/24_0_2_20170116001001063.jpg.chip.jpg'
 '21_32/24_0_2_20170116001001063.jpg.chip.jpg']
['./datasets/archive/UTKFace/45_1_0_20170117154458798.jpg.chip.jpg'
 '44_53/45_1_0_20170117154458798.jpg.chip.jpg']
['./datasets/archive/UTKFace/42_1_3_20170104220806510.jpg.chip.jpg'
 '33_43/42_1_3_20170104220806510.jpg.chip.jpg']
['./datasets/archive/UTKFace/26_1_4_20170116181035930.jpg.chip.jpg'
 '21_32/26_1_4_20170116181035930.jpg.chip.jpg']
['./datasets/archive/UTKFace/45_0_1_20170117165650390.jpg.chip.jpg'
 '44_53/

['./datasets/archive/UTKFace/26_1_1_20170116232602440.jpg.chip.jpg'
 '21_32/26_1_1_20170116232602440.jpg.chip.jpg']
['./datasets/archive/UTKFace/2_1_4_20161221192821980.jpg.chip.jpg'
 '0_2/2_1_4_20161221192821980.jpg.chip.jpg']
['./datasets/archive/UTKFace/56_1_1_20170113012703776.jpg.chip.jpg'
 '54_100/56_1_1_20170113012703776.jpg.chip.jpg']
['./datasets/archive/UTKFace/2_0_0_20170110213227212.jpg.chip.jpg'
 '0_2/2_0_0_20170110213227212.jpg.chip.jpg']
['./datasets/archive/UTKFace/22_0_4_20170117193912061.jpg.chip.jpg'
 '21_32/22_0_4_20170117193912061.jpg.chip.jpg']
['./datasets/archive/UTKFace/21_1_0_20170117142341545.jpg.chip.jpg'
 '21_32/21_1_0_20170117142341545.jpg.chip.jpg']
['./datasets/archive/UTKFace/26_1_1_20170116232657066.jpg.chip.jpg'
 '21_32/26_1_1_20170116232657066.jpg.chip.jpg']
['./datasets/archive/UTKFace/28_0_4_20170105183852672.jpg.chip.jpg'
 '21_32/28_0_4_20170105183852672.jpg.chip.jpg']
['./datasets/archive/UTKFace/65_1_0_20170103175408672.jpg.chip.jpg'
 '54_100/65

['./datasets/archive/UTKFace/26_0_0_20170117172433732.jpg.chip.jpg'
 '21_32/26_0_0_20170117172433732.jpg.chip.jpg']
['./datasets/archive/UTKFace/10_0_0_20170110220447314.jpg.chip.jpg'
 '7_13/10_0_0_20170110220447314.jpg.chip.jpg']
['./datasets/archive/UTKFace/24_1_1_20170112230733998.jpg.chip.jpg'
 '21_32/24_1_1_20170112230733998.jpg.chip.jpg']
['./datasets/archive/UTKFace/33_1_0_20170117174727549.jpg.chip.jpg'
 '33_43/33_1_0_20170117174727549.jpg.chip.jpg']
['./datasets/archive/UTKFace/41_0_4_20170117022116049.jpg.chip.jpg'
 '33_43/41_0_4_20170117022116049.jpg.chip.jpg']
['./datasets/archive/UTKFace/28_1_4_20170103225950647.jpg.chip.jpg'
 '21_32/28_1_4_20170103225950647.jpg.chip.jpg']
['./datasets/archive/UTKFace/41_0_0_20170113184511343.jpg.chip.jpg'
 '33_43/41_0_0_20170113184511343.jpg.chip.jpg']
['./datasets/archive/UTKFace/21_1_4_20161221193306453.jpg.chip.jpg'
 '21_32/21_1_4_20161221193306453.jpg.chip.jpg']
['./datasets/archive/UTKFace/45_0_3_20170119184244311.jpg.chip.jpg'
 '44_

['./datasets/archive/UTKFace/53_1_0_20170110154604352.jpg.chip.jpg'
 '44_53/53_1_0_20170110154604352.jpg.chip.jpg']
['./datasets/archive/UTKFace/55_0_1_20170120134315207.jpg.chip.jpg'
 '54_100/55_0_1_20170120134315207.jpg.chip.jpg']
['./datasets/archive/UTKFace/37_0_2_20170117135956305.jpg.chip.jpg'
 '33_43/37_0_2_20170117135956305.jpg.chip.jpg']
['./datasets/archive/UTKFace/67_0_0_20170117163339177.jpg.chip.jpg'
 '54_100/67_0_0_20170117163339177.jpg.chip.jpg']
['./datasets/archive/UTKFace/29_1_1_20170116023929751.jpg.chip.jpg'
 '21_32/29_1_1_20170116023929751.jpg.chip.jpg']
['./datasets/archive/UTKFace/32_1_0_20170117134816396.jpg.chip.jpg'
 '21_32/32_1_0_20170117134816396.jpg.chip.jpg']
['./datasets/archive/UTKFace/66_0_0_20170120225919754.jpg.chip.jpg'
 '54_100/66_0_0_20170120225919754.jpg.chip.jpg']
['./datasets/archive/UTKFace/26_1_2_20170116161848983.jpg.chip.jpg'
 '21_32/26_1_2_20170116161848983.jpg.chip.jpg']
['./datasets/archive/UTKFace/29_1_0_20170104184312581.jpg.chip.jpg'
 

## Moving the wiki art dataset

In [6]:
import random
import string

def get_random_string(length):
    letters = string.ascii_lowercase
    result_str = ''.join(random.choice(letters) for i in range(length))
    return result_str

In [7]:
dirs = os.listdir('./datasets/face_age/')
wiki_art_files = []
for d in dirs:
    _age = int(d)
    age_slice = None
    for age_str in ages:
        age = age_str.split('_')
        if int(age[0]) <= _age <= int(age[1]):
            age_slice = age_str
    _files = []
    for _file in os.listdir('./datasets/face_age/' + d):
        newName = get_random_string(15)
        ext = _file.split('.')[-1]
        _files.append((
            f'./datasets/face_age/{d}/{_file}',
            f'{age_slice}/{newName}.{ext}'
        ))
    wiki_art_files.extend(_files)
wiki_art_files

[('./datasets/face_age/095/6403.png', '54_100/mjgjnornsuiuwsw.png'),
 ('./datasets/face_age/095/7088.png', '54_100/dzgzjcpvcyxgdgm.png'),
 ('./datasets/face_age/095/5296.png', '54_100/uhqexoyrwxaqpfv.png'),
 ('./datasets/face_age/060/9326.png', '54_100/uxhpffbfgabczih.png'),
 ('./datasets/face_age/060/7133.png', '54_100/nsrsotmtjfmaxpe.png'),
 ('./datasets/face_age/060/3025.png', '54_100/lndfirnjmwtjzsq.png'),
 ('./datasets/face_age/060/4850.png', '54_100/jwlfhjinkrxrbyx.png'),
 ('./datasets/face_age/060/1363.png', '54_100/dqfkutplxgqbqzq.png'),
 ('./datasets/face_age/060/9174.png', '54_100/zzohfgqrnvxbhmi.png'),
 ('./datasets/face_age/060/6784.png', '54_100/rbidgwxsnlnobqt.png'),
 ('./datasets/face_age/060/867.png', '54_100/lexxklfqlbzntdc.png'),
 ('./datasets/face_age/060/568.png', '54_100/vpovyolmmhctwil.png'),
 ('./datasets/face_age/060/8279.png', '54_100/pqkbhuzdjnhjtep.png'),
 ('./datasets/face_age/060/4646.png', '54_100/bllkgulatqeplem.png'),
 ('./datasets/face_age/060/7331.png'

In [9]:
_queue = queue.Queue()
thread = FileCopy(_queue, wiki_art_files, 'train')
thread.start()
while True:
    x = _queue.get()
    if x is None:
        break
    print(x)
thread.join()

('./datasets/face_age/095/6403.png', '54_100/mjgjnornsuiuwsw.png')
('./datasets/face_age/095/7088.png', '54_100/dzgzjcpvcyxgdgm.png')
('./datasets/face_age/095/5296.png', '54_100/uhqexoyrwxaqpfv.png')
('./datasets/face_age/060/9326.png', '54_100/uxhpffbfgabczih.png')
('./datasets/face_age/060/7133.png', '54_100/nsrsotmtjfmaxpe.png')
('./datasets/face_age/060/3025.png', '54_100/lndfirnjmwtjzsq.png')
('./datasets/face_age/060/4850.png', '54_100/jwlfhjinkrxrbyx.png')
('./datasets/face_age/060/1363.png', '54_100/dqfkutplxgqbqzq.png')
('./datasets/face_age/060/9174.png', '54_100/zzohfgqrnvxbhmi.png')
('./datasets/face_age/060/6784.png', '54_100/rbidgwxsnlnobqt.png')
('./datasets/face_age/060/867.png', '54_100/lexxklfqlbzntdc.png')
('./datasets/face_age/060/568.png', '54_100/vpovyolmmhctwil.png')
('./datasets/face_age/060/8279.png', '54_100/pqkbhuzdjnhjtep.png')
('./datasets/face_age/060/4646.png', '54_100/bllkgulatqeplem.png')
('./datasets/face_age/060/7331.png', '54_100/wfhnqxbsledavmx.png

('./datasets/face_age/045/1314.png', '44_53/szrayyyxiklvdci.png')
('./datasets/face_age/045/3645.png', '44_53/litgvuzatoertil.png')
('./datasets/face_age/045/3239.png', '44_53/rfeocruihwnrhrv.png')
('./datasets/face_age/045/4335.png', '44_53/qsxhorskykmagbi.png')
('./datasets/face_age/045/6402.png', '44_53/xdveownprucognv.png')
('./datasets/face_age/045/8770.png', '44_53/mrcmtsbwcdoayqh.png')
('./datasets/face_age/045/9034.png', '44_53/fxeujbfvxkdstld.png')
('./datasets/face_age/045/7630.png', '44_53/acmsdqmkjroodel.png')
('./datasets/face_age/045/812.png', '44_53/bwhchwvmrnogkel.png')
('./datasets/face_age/045/3423.png', '44_53/adcevjvxsvueqey.png')
('./datasets/face_age/045/3666.png', '44_53/oegthxzxbbfbabk.png')
('./datasets/face_age/045/5988.png', '44_53/yhfdizulyaobjhg.png')
('./datasets/face_age/045/5542.png', '44_53/srdfycwgxzgaecq.png')
('./datasets/face_age/045/2617.png', '44_53/xeptgmvvwtqfobi.png')
('./datasets/face_age/045/7038.png', '44_53/zcajtipubkekycz.png')
('./dataset

('./datasets/face_age/051/6713.png', '44_53/bwghuiehojwxqcm.png')
('./datasets/face_age/051/8725.png', '44_53/gqpigsvitgrchal.png')
('./datasets/face_age/051/6783.png', '44_53/asaksiwjofiugjg.png')
('./datasets/face_age/051/8563.png', '44_53/systhcslekknhvf.png')
('./datasets/face_age/051/661.png', '44_53/uoishhzsoywqchf.png')
('./datasets/face_age/051/6834.png', '44_53/bwxqdanxhsvmvlg.png')
('./datasets/face_age/051/6149.png', '44_53/webxshxgjmrctef.png')
('./datasets/face_age/051/7327.png', '44_53/mvwqiezvvfsxxhh.png')
('./datasets/face_age/051/3162.png', '44_53/yirxkahptowbgzf.png')
('./datasets/face_age/051/945.png', '44_53/jumlqhzmarzdyyj.png')
('./datasets/face_age/051/450.png', '44_53/pdmyksgskqsohdc.png')
('./datasets/face_age/051/9767.png', '44_53/cgeybkctifmzpua.png')
('./datasets/face_age/051/1848.png', '44_53/gsvsjoczrapvhnk.png')
('./datasets/face_age/051/9545.png', '44_53/zoeqlbmwncsjaoe.png')
('./datasets/face_age/051/3795.png', '44_53/xkwhdjefbglarjw.png')
('./datasets/

('./datasets/face_age/003/7273.png', '3_6/rrtkwtsbbkndydd.png')
('./datasets/face_age/003/207.png', '3_6/zhdmuctweblwzko.png')
('./datasets/face_age/003/7424.png', '3_6/lqhzuxrwutrtwzr.png')
('./datasets/face_age/003/2144.png', '3_6/mluioyzrghelnwe.png')
('./datasets/face_age/003/6718.png', '3_6/hcwuqxmbmhawoib.png')
('./datasets/face_age/003/8883.png', '3_6/sgtbewuytbeqeth.png')
('./datasets/face_age/003/2061.png', '3_6/upodxulclghqokk.png')
('./datasets/face_age/003/1043.png', '3_6/nvjcmjzwlccdagv.png')
('./datasets/face_age/003/9076.png', '3_6/rowscvclfvkhmuz.png')
('./datasets/face_age/003/7844.png', '3_6/zuqccjbkjtoqpva.png')
('./datasets/face_age/003/8478.png', '3_6/ozmtoxqxvkiyxob.png')
('./datasets/face_age/003/8758.png', '3_6/cmelzguolzfnjif.png')
('./datasets/face_age/003/3214.png', '3_6/qjikumqhfohqeau.png')
('./datasets/face_age/003/6919.png', '3_6/npbztrbuwpbqggu.png')
('./datasets/face_age/003/5117.png', '3_6/sefugnebzmqstcp.png')
('./datasets/face_age/003/5923.png', '3_6

('./datasets/face_age/026/1696.png', '21_32/poraakvupehvuzp.png')
('./datasets/face_age/026/7820.png', '21_32/ptpcmpqygqcjcbe.png')
('./datasets/face_age/026/7335.png', '21_32/spvkbcwiurznjus.png')
('./datasets/face_age/026/7379.png', '21_32/rvudzvmctstxgpe.png')
('./datasets/face_age/026/8028.png', '21_32/rzidqaomnqywvcc.png')
('./datasets/face_age/026/6084.png', '21_32/kndfutwdsnbczsp.png')
('./datasets/face_age/026/4162.png', '21_32/uflbjwajlpeaxtm.png')
('./datasets/face_age/026/2017.png', '21_32/hwkblzskfdijgjv.png')
('./datasets/face_age/026/7650.png', '21_32/mlqggtbtscetyga.png')
('./datasets/face_age/026/3385.png', '21_32/drsuzzzibmpldac.png')
('./datasets/face_age/026/8698.png', '21_32/icbfffhlhzpbmdf.png')
('./datasets/face_age/026/8980.png', '21_32/gaxqpndqrwvlemr.png')
('./datasets/face_age/026/6253.png', '21_32/qmbqbkmvjtvbcaj.png')
('./datasets/face_age/026/6776.png', '21_32/clrmzltfoqiuzyq.png')
('./datasets/face_age/026/2315.png', '21_32/ylbzarbteuqqcjb.png')
('./datase

('./datasets/face_age/008/7823.png', '7_13/bahlbeeytmjnlit.png')
('./datasets/face_age/008/3617.png', '7_13/nlkprvyeqjdupiw.png')
('./datasets/face_age/008/4266.png', '7_13/pynbrqekpjkwiav.png')
('./datasets/face_age/008/2207.png', '7_13/yzaziupooaidjem.png')
('./datasets/face_age/008/7605.png', '7_13/zdbrzhixjlpyvsw.png')
('./datasets/face_age/008/7491.png', '7_13/mlgelkrmgtzwgwq.png')
('./datasets/face_age/008/4278.png', '7_13/dxwbvgqbbwduntf.png')
('./datasets/face_age/008/312.png', '7_13/dgnngxcfhandxhh.png')
('./datasets/face_age/008/9623.png', '7_13/gigrsbgljqteorq.png')
('./datasets/face_age/008/4657.png', '7_13/jhljxpwlzjwdmqs.png')
('./datasets/face_age/008/4248.png', '7_13/cistjfhmgzgdeof.png')
('./datasets/face_age/008/9185.png', '7_13/pjsdjqexyzhiqph.png')
('./datasets/face_age/008/7966.png', '7_13/tnpsoswdnayhqnn.png')
('./datasets/face_age/008/7138.png', '7_13/jvbqgcrnggmwvxf.png')
('./datasets/face_age/008/6179.png', '7_13/anhpozgywzpdrfv.png')
('./datasets/face_age/008/

('./datasets/face_age/040/3122.png', '33_43/arueadjfngtinvy.png')
('./datasets/face_age/040/4333.png', '33_43/cakkkdgymbafqcy.png')
('./datasets/face_age/040/6214.png', '33_43/lqfamusxnwrphyw.png')
('./datasets/face_age/040/9301.png', '33_43/fxdahvygcmrsyhj.png')
('./datasets/face_age/040/6505.png', '33_43/fcecgrjbzzsruya.png')
('./datasets/face_age/040/3074.png', '33_43/uwuypjgxhgrtmbw.png')
('./datasets/face_age/040/3633.png', '33_43/vssmqxaigdjpdix.png')
('./datasets/face_age/040/3036.png', '33_43/xmxzussmfmanhpd.png')
('./datasets/face_age/040/3521.png', '33_43/qvlfkhsbtwiugtk.png')
('./datasets/face_age/040/2222.png', '33_43/wezgvbagiwhuqmx.png')
('./datasets/face_age/040/8854.png', '33_43/mbfujgplqaggohj.png')
('./datasets/face_age/040/6507.png', '33_43/jkuyddfapgpzfxv.png')
('./datasets/face_age/040/7585.png', '33_43/ydkaksyabtovauq.png')
('./datasets/face_age/040/3265.png', '33_43/bxolhhbbbmontff.png')
('./datasets/face_age/040/813.png', '33_43/vbrbsopskjxyceb.png')
('./dataset

('./datasets/face_age/001/9230.png', '0_2/neznjaddmuzisig.png')
('./datasets/face_age/001/4363.png', '0_2/tnbkcbkmhzbitvz.png')
('./datasets/face_age/001/730.png', '0_2/wykipzjqquqleas.png')
('./datasets/face_age/001/7322.png', '0_2/mujmyomsltaazai.png')
('./datasets/face_age/001/2686.png', '0_2/hymwbmakssixkyr.png')
('./datasets/face_age/001/2317.png', '0_2/derokdxfjayxvem.png')
('./datasets/face_age/001/3568.png', '0_2/hxpveqixowvvcqk.png')
('./datasets/face_age/001/2302.png', '0_2/hbrrhlctfekcvor.png')
('./datasets/face_age/001/6904.png', '0_2/bxzcyxtxtbsucnf.png')
('./datasets/face_age/001/3287.png', '0_2/vskqjjqexvezwvr.png')
('./datasets/face_age/001/3641.png', '0_2/nilwraojtgjpbyk.png')
('./datasets/face_age/001/4115.png', '0_2/dbubuuwhsseguar.png')
('./datasets/face_age/001/3887.png', '0_2/pjtdbsscglndfvp.png')
('./datasets/face_age/001/4136.png', '0_2/dquwoiztldiowed.png')
('./datasets/face_age/001/4313.png', '0_2/iyadnxtpwlgoihk.png')
('./datasets/face_age/001/1982.png', '0_2